# Exercice 0

Essayons d'éloigner GB du profil moyen, en faisant GB $\simeq$ Italy.

In [ ]:
base_url = "https://www.imo.universite-paris-saclay.fr/~auder/teachings/analyse-de-donnees/data"
data = read.csv(paste0(base_url,"/table_Nobel.csv"))
# La première colonne contient les noms des pays = labels des lignes
row.names(data) = data[,1]
data = data[,-1]

GBIndex = (1:nrow(data)) [row.names(data) == "GB"] #4
ItalyIndex = (1:nrow(data)) [row.names(data) == "Italie"] #5
data2 = data #R fera une copie quand on modifiera data2
data2[GBIndex,] = data[ItalyIndex,] + rpois(ncol(data),3) - 3

library(FactoMineR)
res.ca = CA(data2, graph=FALSE)

In [ ]:
options(repr.plot.width=15, repr.plot.height=10)
plot(res.ca)

Sans surprises, la Grande-Bretagne se retrouve du côté de l'Italie (fluctuations possibles dues à rpois). Le reste est à peu près inchangé.

Ensuite, on peut vérifier l'affirmation comme quoi les résultats sont inchangés en fusionnant des lignes proportionnelles : fusionnons Italie et Grande-Bretagne après avoir tracé le graphe où ces deux lignes sont proportionnelles.

In [ ]:
data2[GBIndex,] = 2 * data[ItalyIndex,]
res.ca_split = CA(data2, graph=FALSE)
data2[ItalyIndex,] = 3 * data[ItalyIndex,]
data2[GBIndex,] = data2[nrow(data),] #USA
data2 = data2[-nrow(data),]
row.names(data2)[GBIndex] = "USA"
res.ca_fusion = CA(data2, graph=FALSE)

In [ ]:
library(gridExtra)
library(ggplot2)
plot1 = plot(res.ca_split)
plot2 = plot(res.ca_fusion)
grid.arrange(plot1, plot2, ncol=2)

Les graphes sont bien identiques.

# Exercice 1

In [ ]:
data = read.csv(paste0(base_url,"/MAMe_dataset.csv"))
head(data)

A priori, seules les colonnes Medium (type de toile) et Museum (nom du musée) sont qualitatives. Ceci dit, toute variable quantitative peut être considérée qualitative en la découpant en classes. Par exemple ici on pourrait considérer "aspect ratio < 1 = portrait" et "aspect ratio > 1 = paysage". On perdrait de l'information au passage donc il faudrait par exemple compléter par une ACP.

On considère ici seulement Medium vs. Museum.

In [ ]:
data_tbl = table(subset(data, select=c("Medium","Museum")))
res.ca = CA(data_tbl, graph=FALSE)

In [ ]:
plot(res.ca)

Il semble y avoir (relativement) plus de Lithographs au musée de Cleveland, et plus de Hand-colored engravings à celui de LA. vérifions numériquement :

In [ ]:
indices = row.names(data_tbl) %in% c("Lithograph","Hand-colored engraving")
data_tbl[indices,]

Chose intéressante, la ligne Lithograph est plutôt du côté du musée de Cleveland, mais il y a autant de telles oeuvres au musée métropolitain. A priori expliqué par le fait que les types de tableaux du côté du musée métropolitain ont proportionnellement beaucoup plus d'oeuvres dans ce musée.

En tout cas on n'y voit pas très clair...

In [ ]:
# Cherchons à regrouper les lignes similaires (résultat quasi inchangé, plus lisible)
proportions = t(apply(data_tbl, 1, function(row) row / sum(row)))
k = kmeans(proportions, 6) #6 trouvé par "essais-erreurs"

In [ ]:
reduced_table = t(sapply(1:6, function(i) {
    inds = (1:nrow(data_tbl))[k$cluster == i]
    if (length(inds)>1) {colSums(data_tbl[inds,])} else {data_tbl[inds,]}
}))
row.names(reduced_table) = sapply(1:6, function(i) {
    inds = (1:nrow(data_tbl))[k$cluster == i]
    Reduce(function(x,y) paste(x, y, sep=";"), row.names(data_tbl)[inds])
})

In [ ]:
rbind(reduced_table, colMeans(reduced_table)) #profil moyen en bas

In [ ]:
res.ca = CA(reduced_table, graph=FALSE)
plot(res.ca)

Conformément aux résultats numériques, Albumen photograph;Clay;Hand-colored etching;Pen and brown ink;Silk and metal thread;Woven fabric + Faience;Glass;Ivory;Limestone;Steel;Wood + Graphite;Iron;Marble;Polychromed wood caractérisent plutôt le musée métropolitain. La variable regroupée Gold;Porcelain;Silver;Wood engraving;Woodcut  semblait aussi devoir être du côté du Metropolitan Museum, mais il y aussi beaucoup de telles toiles au Cleveland Museum, donc la variable n'a au final pas de direction précise. Enfin, Bronze;Ceramic;Engraving;Etching;Lithograph;Oil on canvas;Woodblock est plutôt à droite bien que ses proportions soient équilibrées (~33%). En effet le centre de gravité est biaisé vers le Metropolitan Museum.

# Exercice 2

In [ ]:
data = read.csv(paste0(base_url,"/paintings.csv"))
head(data)

La dernière colonne "painting" désigne la toile, et est a priori unique => identifiant. Vérifions :

In [ ]:
nrow(data) ; length(unique(data$painting))

Les colonnes 1 à 48 contiennent les notes (de 1 à 5) attribuées par 48 étudiants à l'ensemble des 30 oeuvres. Une première idée consisterait à regarder les corrélations entre mouvement artistique et artiste. Ce n'est pas une super idée pour deux raisons :
 - un artiste peint a priori la plupart de ses toiles conformément à un unique mouvement ;
 - dans cette base chaque artiste n'est présent qu'une fois :

In [ ]:
length(unique(data$artist))

Reste donc à étudier soit les corrélations inter-étudiants (why not), ou les affinités de chaque étudiant avec les mouvements artistiques. Comparons par exemple S4 à S23 puis S12 à art.movement.

In [ ]:
t1 = table(subset(data, select=c("S4","S23")))
res.ca = CA(t1, graph=FALSE)
plot(res.ca)

Visuellement, on pourrait dire que quand l'un note 4 l'autre a tendance à noter 3, de même pour 3 / 5, 5 / 2 et 1 / 1 (attention l'ordre importe !). Numériquement c'est nettement plus flou :

In [ ]:
t1

En effet hormis l'association assez ntette 1 / 1 (les deux ont tendance à détester les mêmes oeuvres), rien ne se détache vraiment surtout compte-tenu du faible nombre de lignes. On vérifie tout de même dans une certaine mesure 5 / 2 (seulement).

In [ ]:
t2 = table(subset(data, select=c("S12","art.movement")))
res.ca = CA(t2, graph=FALSE)
plot(res.ca)

Cet étudiant semble plutôt versé dans l'art nouveau et dans une moindre mesure l'impressionisme. Il apprécie assez Pop art/Romanticism/Post-Impressionism et a tendance à ne pas aimer le reste. Vérifions.

In [ ]:
t(t2)

Pas évident de juger tout à l'oeil :

In [ ]:
rowMeans(t2[,c("Art Nouveau","Impressionism")])
rowMeans(t2[,c("Pop art","Romanticism","Post-Impressionism")])
rowMeans(t2[,c("Abstract art","Baroque","Cubism","Nbeoclassicism","Op art","Renaissance","Surrealism","Symbolism")])

=> À peu près OK avec l'analyse.